# Formules Logiques

Marc Lorenzi - 20 avril 2018

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline
import random, sys

## 1. Syntaxe des formules

### 1.1 Notion de formule

On se donne un ensemble $\mathcal V$ dont les éléments sont appelés les __variables propositionnelles__. La nature exacte de $\mathcal V$ n'a pas d'importance. De façon informelle, lorsque nous aurons besoin de variables nous les noterons $x, y, z, a, b, a_0$, etc. 

On pose également $\mathcal S = \{-, +, ., \rightarrow, \leftrightarrow\, (, )\}$. Nous appellerons formule toute suite de symboles (les informaticiens disent "chaîne de caactères", les théoriciens disent "mot") de $\mathcal V \cup \mathcal S$ vérifiant les propriétés suivantes :

- Les éléments de $\mathcal V$ sont des formules.
- Si $f$ est une formule, $-f$ est une formule.
- Si $f_1$ et $f_2$ sont des formules, $(f_1 . f_2)$ est une formule.
- Si $f_1$ et $f_2$ sont des formules, $(f_1 + f_2)$ est une formule.
- Si $f_1$ et $f_2$ sont des formules, $(f_1 \rightarrow f_2)$ est une formule.
- Si $f_1$ et $f_2$ sont des formules, $(f_1 \leftrightarrow f_2)$ est une formule.

"$-$" est le __connecteur unaire__ (il symbolise la négation). "$+$", "$.$", "$\rightarrow$" et "$\leftrightarrow$" sont les __connecteurs binaires__. Le point symbolise le "et", le $+$ représente le "ou", et les flèches $\rightarrow$ et $\leftrightarrow$ représentent l'implication et l'équivalence. Le choix des symboles de connecteurs est guidé par le fait qu'ils sont faciles à entrer au clavier. 

On adopte également des conventions de priorité qui permettent de ne pas écrire certaines parenthèses : les connecteurs, du plus prioritaire au moins prioritaire, sont $-, ., +, \rightarrow, \leftrightarrow$. Ainsi, par exemple, $(x\rightarrow y)+(y\rightarrow z)\leftrightarrow (x\rightarrow z)$ est une façon abrégée d'écrire la formule $(((x\rightarrow y)+(y\rightarrow z))\leftrightarrow (x\rightarrow z))$.

### 1.2 Représenter les formules en Python

Nous allons dans ce notebook écrire des fonctions qui prennent des formules en paramètre, qui calculent des formules, qui les combient entre-elles ... Il s'agit d'avoir une représentation des formules dans notre langage préféré qui nous permette de les manipuler efficacement. Cette formule est elle un "et" ? Une implication ? Quelles sont ses variables ? etc.

On peut distinguer trois sortes de formules.

- Les variables. Nous les représenterons par un couple `('var', x)` où $x$ est une chaîne de caractères, qui est le nom proprement dit de la variable.
- La négation d'une formule. Nous représenterons une négation par le couple `('not', f1)` où $f_1$ est elle même la représentation d'une formule.
- Les formules "binaires". Nous représenterons une telle formule par un triplet `(symb, f1, f2)` où `symb` peut prendre les valeurs `and`, `or`, `imp` et `eqv` (et, ou, implication et équivalence).

Voici un exemple, la représentation de la formule $(x\rightarrow y)+(y\rightarrow z)\leftrightarrow (x\rightarrow z)$.

In [ ]:
exemple = ('eqv', 
     ('and', ('imp', ('var', 'x'), ('var', 'y')), 
             ('imp', ('var', 'y'), ('var', 'z'))
     ), 
     ('imp', ('var', 'x'), ('var', 'z')))

On voit tout de suite apparaître deux problèmes pratiques :

1. C'est impossible à lire.
2. C'est impossible à écrire.

Nous allons petit à petit régler ces deux problèmes.

### 1.3 Affichage des formules

Résolvons déjà le premier problème : l'affichage d'une formule. Nous allons écrire une fonction qui, étant donnée une formule $f$, renvoie une représentation de $f$ sous forme d'une chaîne de caractères lisible par un être humain (enfin par un logicien).

Voici deux fonctions évidentes. Pour une formule $f$ de type `('not', g)`, `left(f)` renvoie $g$. Pour une formule binaire, `left` et `right` renvoient les constituants de la formule. 

In [ ]:
def left(f): return f[1]
def right(f): return f[2]

In [ ]:
left(exemple)

In [ ]:
right(exemple)

Le dictionnaire `symbol` contient la représentation symbolique de chacun des connecteurs.

In [ ]:
symbol = {'not': '-', 'and': '.', 'or': '+', 'imp': '->', 'eqv': '<->'}

In [ ]:
symbol['eqv']

Le dictionnaire `prio` contient les priorités de tous les connecteurs. On a également assigné une priorité maximale aux variables.

In [ ]:
prio = {'var': 15, 'not': 10, 'and': 8, 'or': 6, 'imp': 4, 'eqv': 2}

La fonction `paren` prend en paramètres une chaîne de caractères $s$ et deux formules. Selon la priorité relative de ces formules, elle renvoie la chaîne $s$ entre parenthèses ou pas.

In [ ]:
def paren(s, f1, f):
    if prio[f1[0]] <= prio[f[0]]: return '(' + s + ')'
    else: return s

Et voici enfin la fonction `to_string`. Elle prend une formule $f$ en paramètre et renvoie une chaîne qui est une forme "humainement lisible" de la formule. Le code est simple, étudiez-le. En particulier, comprenez à quoi sert l'appel à `paren`.

In [ ]:
def to_string(f):
    if f[0] == 'var': return f[1]
    elif f[0] == 'not': 
        f1 = left(f)
        s1 = to_string(f1)
        return '-' + paren(s1, f1, f)
    else:
        smb = symbol[f[0]]
        f1 = left(f)
        f2 = right(f)
        s1 = to_string(f1)
        s2 = to_string(f2)
        return paren(s1, f1, f) + smb + paren(s2, f2, f)

In [ ]:
to_string(exemple)

In [ ]:
exemple

### 1.4 Hauteur d'une formule

La hauteur $h(f)$ d'une formule $f$ est définie comme suit :

- La hauteur d'une variable est 0.
- Si $f =-f_1$, alors $h(f)=1+h(f_1)$.
- Si $f =f_1 \alpha f_2$, où $\alpha$ est un connecteur binaire alors $h(f)=1+\max(h(f_1), h(f_2))$.

Pourquoi appeler cela "hauteur" ? Lorsque nous verrons qu'à chaque formule on peut associer un arbre, on comprendra mieux. Ou alors, si on a déjà lu le notebook sur les arbres, on a déjà compris.

In [ ]:
def hauteur(f):
    if f[0] == 'var': return 0
    elif f[0] == 'not' : return 1 + hauteur(left(f))
    else:
        h1 = hauteur(left(f))
        h2 = hauteur(right(f))
        return 1 + max([h1, h2])

In [ ]:
hauteur(exemple)

### 1.5 Formules "aléatoires"

Pour tester les fonctions que nous allons écrire, il peut être intéressant de pouvoir fabriquer des formules un peu n'importe comment et très très compliquées. La fonction ci-dessous renvoie une formule "aléatoire" de hauteur $h$ dont les variables sont $a_0,a_1,\ldots,a_{n-1}$.

In [ ]:
def formule_aleatoire(h, n):
    if h == 0:
        p = random.randint(0, n - 1)
        return ('var', 'a' + str(p))
    else:
        f1 = formule_aleatoire(h - 1, n)
        p = random.randint(0, 4)
        if p == 0: return ('not', f1)
        else:
            h1 = random.randint(0, h - 1)
            f2 = formule_aleatoire(h1, n)
            b = random.randint(0, 1)
            if b == 1: f1, f2 = f2, f1
            if p == 1: return ('and', f1, f2)
            elif p == 2: return ('or', f1, f2)
            elif p == 3: return ('imp', f1, f2)
            else: return ('eqv', f1, f2)

In [ ]:
f = formule_aleatoire(10, 5)
to_string(f)

In [ ]:
f

In [ ]:
hauteur(f)

Ben oui c'est normal.

### 1.6 Arbre associé à une formule

Je vais ici supposer que vous avez jeté un coup d'oeil au notebook sur les arbres. Je ne reprendrai pas la définition de racine, de fils, de noeud, de feuille, etc. Si ce qui suit est d'une obscurité totale pour vous, sautez les explications et foncez à l'exemple !

Eh oui, une formule, par exemple $f_1 + f_2$ peut être vue comme un arbre dont la racine est $+$ et les deux fils sont les arbres associés aux formules $f_1$ et $f_2$. Selon le type de la formule $f$, l'arbre qui la représente a différentes formes :

- si $f$ est une variable $x$, l'arbre a juste un noeud, d'étiquette $x$.
- Si $f =-g$, l'arbre a une racine étiquetée par $\tilde{}$ et un seul fils qui est l'arbre qui représente $g$.
- Si $f=f_1 . f_2$,  l'arbre a une racine étiquetée par $.$ et deux fils qui sont les arbre qui représentent $f_1$ et $f_2$. Et de même pour les autres connecteurs binaires.

La fonction `draw(f)` ci-dessous dessine l'arbre qui représente la formule `f`. Elle utilise une fonction auxiliaire `draw_aux`. Dans le notebook sur les arbres apparaissent des fonctions quasiment identiques.

In [ ]:
def draw_aux(f, rect, dy):
    x1, x2, y1, y2 = rect
    xm = (x1 + x2) // 2
    if f[0] == 'var': noeud = f[1]
    else: noeud = symbol[f[0]]
    plt.text(xm + 3, y2, noeud, fontsize=12, horizontalalignment='left',verticalalignment='bottom')
    if f[0] == 'var': return
    if f[0] == 'not':
        draw_aux(left(f), (x1, x2, y1, y2 - dy), dy)
        a, b = ((xm, xm), (y2, y2 - dy))
        plt.plot(a, b, 'k', marker='o')
    else:
        draw_aux(left(f), (x1, xm, y1, y2 - dy), dy)
        draw_aux(right(f), (xm, x2, y1, y2 - dy), dy)
        a, b = ((xm, (x1 + xm) // 2), (y2, y2 - dy))
        plt.plot(a, b, 'k', marker='o')
        c, d = ((xm, (x2 + xm) // 2), (y2, y2 - dy))
        plt.plot(c, d, 'k', marker='o')

In [ ]:
def draw(f):
    d = 512
    pad = 20
    dy = (d - 2 * pad) / (hauteur(f))
    draw_aux(f, (pad, d - pad, pad, d - pad), dy)
    plt.axis([0, d, 0, d])
    plt.axis('off')
    plt.show()

La ligne suivante, c'est pour que nos arbres soient affichés assez gros à l'écran.

In [ ]:
plt.rcParams['figure.figsize'] = (12, 8)

Testons `draw` ...

In [ ]:
draw(exemple)

In [ ]:
f = formule_aleatoire(6, 5)
draw(f)

### 1.7 Les variables d'une formule

Quelles sont les variables qui interviennent dans une formule ? La fonction ci-dessous résout le problème.

In [ ]:
def variables(f):
    if f[0] == 'var': return set([f[1]])
    elif f[0] == 'not': return variables(f[1])
    else: return variables(f[1]).union(variables(f[2]))

In [ ]:
variables(exemple)

In [ ]:
variables(formule_aleatoire(8, 6))

## 2. Un analyseur syntaxique

#### Ce paragraphe n'est pas facile. Il peut être sauté sans honte en première lecture.

L'ensemble des formules logiques est un langage, c'est à dire un ensemble de mots, dont les lettres appartiennent à l'alphabet $\mathcal A = \mathcal V\cup\mathcal S$ que nous avons défini au début de ce notebook. Étant donné un mot sur l'alphabet $\mathcal A$ qui représente une formule valide, nous voudrions décrire un algorithme qui permet de l'analyser pour en déduire la représentation en Python de la formule. Histoire de compliquer un peu les choses, on autorise un parenthésage "minimal". 

La tâche paraît ardue.

### 2.1 Premier jet

Appelons irréductible toute formule qui ne contient que des parenthèses, des "not", et une variable. Une telle formule peut être de trois sortes :

- $x$, où $x$ est une variable
- $(f)$ où $f$ est une formule irréductible
- $-f$ où $f$ est irréductible. 

On peut résumer cela par la ligne

`I ::= -I  | V | (I)`

La barre verticale signifie "ou bien", $V$ et $I$ signifient respectivement "variable" et "formule irréductible"

La fonction `parseI` ci-dessous prend une chaîne de caractères $s$ en paramètre. Elle renvoie un couple $(f, r)$ où $f$ est le formule irréductible représentée par le plus petit __préfixe__ possible de $s$, et $r$ est la partie de $s$ qui n'a servi à rien (c'est un __suffixe__ de $s$).

__Remarque__ : un préfixe d'une chaîne de caractères $s$ est une chaîne constituée des premières lettres de $s$. Par exemple, les préfixes de 'bonjour' sont '', 'b', 'bo', 'bon', ..., 'bonjour'. Un préfixe de $s$ différent $s$ est dit __strict__. On définit bien sûr de même la notion de __suffixe__. 

In [ ]:
def parseI(s):
    if s[0] == '(':
        f, reste = parseI(s[1:])
        assert reste[0] == ')'
        return (f, reste[1:])
    elif s[0] == '-':
        f, reste = parseI(s[1:])
        return (('not', f), reste)
    else:
        return (('var', s[0]), s[1:])

Par exemple, prenons $s=--(-((x)))(y\to z)$. La partie intéressante du début de $s$ est $--(-((x)))$. Le reste est $(y\to z)$.

In [ ]:
parseI('--(-((x)))(y->z)')

### 2.2 On complique un peu

Tâchons maintenant d'analyser des formules contenant des "et", des "not", des variables et des parenthèses. Une formule de cette sorte est essentiellement

- une formule irréductible, ou bien
- une formule irréductible "et" une autre formule de cette sorte

Notons `E4` une telle formule : `E4 ::= I . E4 | I`

Oui, d'accord, à condition de redéfinir `I`en : `I ::= -I  | V | (E4)`. Eh oui, une expression de type `E4` avec une paire de parenthèses englobantes doit être considérée comme irréductible ! Le code Python devient donc :

In [ ]:
def parse4(s):
    f, reste = parseI(s)
    if len(reste) >= 1 and reste[0] == '.':
        f1, reste1 = parse4(reste[1:])
        return (('and', f, f1), reste1)
    else:
        return (f, reste)

In [ ]:
def parseI(s):
    if s[0] == '(':
        f, reste = parse4(s[1:])
        assert reste[0] == ')'
        return (f, reste[1:])
    elif s[0] == '-':
        f, reste = parseI(s[1:])
        return (('not', f), reste)
    else:
        return (('var', s[0]), s[1:])

Testons ...

In [ ]:
parse4('a.(a.-b)c->d')

Le premier préfixe de notre exemple qui est de type `E4` est correctement analysé, et tout ce qui suit est renvoyé sans y toucher. 

### 2.3 On rajoute les $+$

Attaquons nous à l'analyse des formules contenant des "ou", des "et", des "not", des variables et des parenthèses. Une formule de cette sorte est essentiellement

- une formule du type `E4`, ou bien
- une formule du type `E4` "ou" une autre formule de cette sorte

Notons `E3` une telle formule : `E3 ::= E4 . E3 | E4`

Pourquoi cela fonctionne-t-il ? parce que le "et" est prioritaire par rapport au "ou" !

Le code Python devient donc :

In [ ]:
def parse3(s):
    f, reste = parse4(s)
    if len(reste) >= 1 and reste[0] == '+':
        f1, reste1 = parse3(reste[1:])
        return (('or', f, f1), reste1)
    else:
        return (f, reste)

In [ ]:
def parse4(s):
    f, reste = parseI(s)
    if len(reste) >= 1 and reste[0] == '.':
        f1, reste1 = parse4(reste[1:])
        return (('and', f, f1), reste1)
    else:
        return (f, reste)

In [ ]:
def parseI(s):
    if s[0] == '(':
        f, reste = parse4(s[1:])
        assert reste[0] == ')'
        return (f, reste[1:])
    elif s[0] == '-':
        f, reste = parseI(s[1:])
        return (('not', f), reste)
    else:
        return (('var', s[0]), s[1:])

Testons ...

In [ ]:
parse3('a.b+-(c.d)+e->f')

Le premier préfixe de notre exemple qui est de type `E3` est correctement analysé, et tout ce qui suit, c'est à dire $\to f$, est renvoyé sans y toucher. 

### 2.4 On rajoute implications et équivalences

Rajouter les derniers connecteurs ne pose pas de problème supplémentaires. Il faut juste prendre garde à leur priorité : les moins prioritaires d'abord. Appelons `E1` le type des formules qui sont des équivalences et `E2` le type des formules qui sont des implications. Voici enfin la __grammaire__ complète des formules : 

`E1 ::= E2 <-> E1 | E2`

`E2 ::= E3 ->  E2 | E3`

`E3 ::= E4  +  E3 | E4`

`E4 ::= I   .  E4 | I`

`I ::= -I  | V | (E1)`

Je vous suggère d'écrire quelques formules et de réfléchir à la question avant de poursuivre ...

Notre analyseur de formules est donc composé de 5 fonctions, une pour chaque ligne de la grammaire. Chacune des fonctions appelle la fonction de numéro "un de plus", sauf la dernière qui peut se permettre d'appeler la première. Oui, nous avons là 5 fonctions mutuellement récursives.

Chacune de ces fonctions prend en paramètre une chaine de caractères $s$. Elle analyse le début de $s$ jusqu'à trouver une formule bien formée pour la fonction en question. Puis la fonction renvoie un couple formé de la formule trouvée et du reste non analysé de $s$.

In [ ]:
def parse1(s):
    f, reste = parse2(s)
    if len(reste) >= 3 and reste[0:3] == '<->':
        f1, reste1 = parse1(reste[3:])
        return (('eqv', f, f1), reste1)
    else:
        return (f, reste)

In [ ]:
def parse2(s):
    f, reste = parse3(s)
    if len(reste) >= 2 and reste[0:2] == '->':
        f1, reste1 = parse2(reste[2:])
        return (('imp', f, f1), reste1)
    else:
        return (f, reste)

In [ ]:
def parse3(s):
    f, reste = parse4(s)
    if len(reste) >= 1 and reste[0] == '+':
        f1, reste1 = parse3(reste[1:])
        return (('or', f, f1), reste1)
    else:
        return (f, reste)

In [ ]:
def parse4(s):
    f, reste = parseI(s)
    if len(reste) >= 1 and reste[0] == '.':
        f1, reste1 = parse4(reste[1:])
        return (('and', f, f1), reste1)
    else:
        return (f, reste)

In [ ]:
def parseI(s):
    if s[0] == '(':
        f, reste = parse1(s[1:])
        assert reste[0] == ')'
        return (f, reste[1:])
    elif s[0] == '-':
        f, reste = parseI(s[1:])
        return (('not', f), reste)
    else:
        return (('var', s[0]), s[1:])

Pour analyser la chaîne $s$, on appelle `parse1`, qui renvoie un couple $(f, r)$ et on laisse tomber $r$ ... qui devrait être la chaîne vide. Disons-le clairement, cet analyseur n'est pas bien solide :

- il n'accepte que des variables propositionnelles de 1 caractère
- il ne supporte pas les espaces
- il ne fait aucun effort pour détecter les erreurs de syntaxe

Mais il suffira pour ce que nous voulons en faire : taper rapidement des exemples.

In [ ]:
def parse(s):
    f, reste = parse1(s)
    return f

Testons !

In [ ]:
f = parse('(x->y)+(y->z)<->x->z')
f

In [ ]:
draw(f)

In [ ]:
f = parse('x->--x+-(y.z)')
f

In [ ]:
draw(f)

Vous pouvez maintenant très facilement utiliser avec Python vos formules logiques préférées.

## 3. Disséquer les formules

Juste pour voir ... Voici quelques illustrations de ce que nous pouvons faire avec notre représentation des formules.

### 3.1 Éliminer les implications et les équivalences

Voici une fonction qui prend en paramètre une formule $f$ et renvoie une formule $f'$ équivalente à $f$ qui ne contient ni le connecteur $\rightarrow$ ni le connecteur $\leftrightarrow$. Comment faire cela ? Facile, en utilisant les équivalences classiques. On sait que $f_1 \rightarrow f_2\equiv (- f_1 + f_2)$ et $f_1 \leftrightarrow f_2\equiv (- f_1 + f_2).(- f_2 + f_1)$. Une fonction récursive s'impose.

In [ ]:
def et_ou(f):
    if f[0] == 'var': return f
    elif f[0] == 'not': return ('not', et_ou(left(f)))
    else:
        f1 = et_ou(left(f))
        f2 = et_ou(right(f))
        if f[0] == 'and': return ('and', f1, f2)
        elif f[0] == 'or': return ('or', f1, f2)
        elif f[0] == 'imp': return ('or', ('not', f1), f2)
        elif f[0] == 'eqv': return ('and',('or', ('not', f1), f2),('or', ('not', f2), f1))

In [ ]:
to_string(et_ou(exemple))

In [ ]:
draw(et_ou(exemple))

### 3.2 La forme prénexe

Une formule est dite sous forme __prénexe__ lorsque les seuls symboles de n'égation intervenant dans la formule le sont devant des variables. La fonction ci-dessous prend une formule $f$ ne contenant ni "implique" ni "équivaut" et renvoie une formule équivalente à $f$ sous forme prénexe. Comment faire ? Eh bien les lois de Morgan $- (f_1 . f2)\equiv - f_1 + - f_2$ et $- (f_1 + f2)\equiv - f_1 . - f_2$ ainsi que la loi $--f\equiv f$ sont nos amies ...

__Remarque__ : à la fin de ce notebook nous serons en mesure de ___démontrer___ en Python que les lois de Morgan (et toutes les formules que nous voulons) sont des tautologies.

In [ ]:
def prenexe(f):
    if f[0] == 'var': return f
    elif f[0] == 'not':
        f1 = left(f)
        if f1[0] == 'var': return ('not', f1)
        elif f1[0] == 'not': return prenexe(left(f1))
        else:
            g1 = prenexe(('not', left(f1)))
            g2 = prenexe(('not', right(f1)))
            if f1[0] == 'and': return ('or', g1, g2)
            else: return ('and', g1, g2)
    else:
        f1 = prenexe(left(f))
        f2 = prenexe(right(f))
        if f[0] == 'and': return ('and', f1, f2)
        else: return ('or', f1, f2)

In [ ]:
to_string(prenexe(et_ou(exemple)))

In [ ]:
draw(prenexe(et_ou(exemple)))

In [ ]:
f = prenexe(et_ou(formule_aleatoire(8, 4)))
to_string(f)

In [ ]:
draw(f)

### 3.3 Substitution

Soit $f$ une formule. Soit $x$ une variable. Soit $g$ une autre formule. Comment substituer $g$ à $x$ dans la formule $f$ ? Du code Python sera aussi clair qu'une longue explication.

In [ ]:
def substituer(f, x, g):
    if f[0] == 'var':
        if f[1] == 'x': return g
        else: return f
    elif f[0] == 'not':
        return ('not', substituer(left(f), x, g))
    else:
        return (f[0], substituer(left(f), x, g), substituer(right(f), x, g))

In [ ]:
f = parse('x->(y->x)')
g = parse('a.b')
to_string(substituer(f, 'x', g))

On pourrait continuer longtemps. Ce n'est évidemment pas la fin de l'histoire mais j'espère vous avoir montré que plus rien ne nous résiste concernant la __syntaxe__ des formules. Nous allons passer maintenant à autre chose, la __sémantique__. Une formule est-elle vraie ou fausse ? 

## 4. Sémantique: évaluation des formules

Disons-le tout de suite : une formule n'est NI vraie NI fausse. Faisons un parallèle avec les formules de l'algèbre. Considérons $A=x+y.z$, où $x,y,z\in\mathbb R$. Que vaut $A$ ? C'est évidemment une question idiote. La réponse est : "ça dépend !". Oui, et de quoi ? Eh bien de $x, y$ et $z$.

Maintenant si je vous dit que $x=2$, $y=3$ et $z=4$, alors vous me direz que $A$ vaut $15$. Et vous aurez tort, ça vaut 14 :-). Bref, une formule ne vaut quelque chose que lorsque ses variables valent quelque chose. Pour évaluer une formule nous devons être dans un certain __environnement__. Revenons aux formules logiques et soyons précis :

__Définition__ : un environnement est une fonction $\gamma : \mathcal V\to\{0, 1\}$.

Le choix de $\{0, 1\}$ est arbitraire. Moralement, 0 signifie "faux" et 1 signifie "vrai", mais toute autre __interprétation__ est possible. Le mot est lâché. Sens ? Signification ? Interprétation ? Nous ne pouvons plus nous contenter d'écrire des formules, nous voulons en plus leur donner un sens. C'est le but de la __sémantique__.

Je n'irai pas plus avant dans la théorie. Pour faire court, on peut montrer que pour tout environnement $\gamma$, pour toute formule $f$, il existe une valeur dans $\{0, 1\}$ dépendant de $f$ et $\gamma$, pour laquelle les connecteurs apparaissant dans $f$ ont le comportement que l'on souhaite. On note cette valeur ${\text eval}(f, \gamma)$. Par exemple, il est souhaitable que ${\text eval}(f_1.f_2, \gamma)$ soit égal à ${\text eval}(f_1,\gamma)\times{\text eval}(f_2,\gamma)$ pour repecter ce que l'on pense du "et" (faux et faux = faux, faux et vrai = faux, etc.). 


On montre également que cette valeur ne dépend que de la valeur de $\gamma$ en les variables qui apparaissent dans $f$.

### 4.1 Codes de longueur n

Étape 1 : fabriquer tous les $n$-uplets de 0 et de 1, pour un $n$ donné.

In [ ]:
def codes(n):
    if n == 0: return [[]]
    else:
        cs = codes(n - 1)
        return [[0] + c for c in cs] + [[1] + c for c in cs]

In [ ]:
codes(4)

### 4.2 Environnements

Étape 2 : fabriquer tous les environnements possibles pour une liste donnée de variables.

In [ ]:
def environnement(vs, c):
    gamma = {}
    for i in range(len(vs)):
        gamma[vs[i]] = c[i]
    return gamma

In [ ]:
environnement(['x', 'y', 'z'], [0, 1, 0])

In [ ]:
def environnements(vs):
    n = len(vs)
    cs = codes(n)
    return [environnement(vs, c) for c in cs]

In [ ]:
environnements(list(variables(exemple)))

### 3.3 Évaluer une formule dans un environnement

Nous y voilà. Voici la fonction d'évaluation. La comprendre, c'est la lire. Les formules pour l'implication et l'équivalence peuvent paraître absconses, vérifiez-les.

In [ ]:
def eval(f, gamma):
    if f[0] == 'var': return gamma[f[1]]
    elif f[0] == 'not':
        b = eval(f[1], gamma)
        return 1 - b
    else:
        b1 = eval(f[1], gamma)
        b2 = eval(f[2], gamma)
        if f[0] == 'and': return b1 * b2
        elif f[0] == 'or': return b1 + b2 - b1 * b2
        elif f[0] == 'imp': return 1 - b1 + b1 * b2
        elif f[0] == 'eqv': return 1 - b1 - b2 + 2 * b1 * b2        

Voici l'évaluation de notre exemple fétiche sur tous les environnements possibles.

In [ ]:
env = environnements(list(variables(exemple)))
[(gamma, eval(exemple, gamma)) for gamma in env]

### 3.4 Table de vérité

La fonction ci-dessous ne fait qu'afficher sous forme plus "lisible" le résultat que nous avons obtenu ci-dessus. On range tout cela dans ce que l'on appelle "la" table de vérité de la formule.

In [ ]:
def afficher_table(f):
    vars = list(variables(f))
    vars.sort()
    env = environnements(vars)
    for x in env[0]: sys.stdout.write('%3s' % x) # étiquettes de la table de vérité
    sys.stdout.write('%3s\n'% 'f') # la dernière étiquette
    for gamma in env:
        b = eval(f, gamma)
        for x in gamma: sys.stdout.write('%3d' % gamma[x])
        sys.stdout.write('%3d\n' % b)

In [ ]:
afficher_table(exemple)

In [ ]:
afficher_table(formule_aleatoire(10, 4))

### 3.5 Satisfiabilité, tautologies, contradictions

Ce notebook est déjà bien long. Je me contenterai de finir en disant deux mots sur la satisfiabilité.

__Définition__ : soient $f$ une formule et $\gamma$ un environnement. On dit que $\gamma$ satisfait $f$ (ou que $f$ est satisfaite par $\gamma$) lorsque ${\text eval}(f,\gamma)=1$.

__Définition__ : Une formule est satisfiable lorsqu'il existe un environnement qui la satisfait.

__Définition__ : Une formule est une contradiction lorsqu'aucun environnement ne la satisfait.

__Définition__ : Une formule est une tautologie lorsque tous les environnements la satisfont.

Une tautologie est donc une formule très satisfaite :-).

In [ ]:
def satisfiable(f):
    vars = list(variables(f))
    env = environnements(vars)
    for gamma in env:
        if eval(f, gamma) == 1: return (True, gamma)
    return (False, None)

In [ ]:
f = parse(('x->(y->x)'))
satisfiable(f)

In [ ]:
def contradiction(f):
    return not satisfiable(f)

In [ ]:
def tautologie(f):
    vars = list(variables(f))
    env = environnements(vars)
    for gamma in env:
        if eval(f, gamma) == 0: return False
    return True

In [ ]:
tautologie(f)

In [ ]:
f = formule_aleatoire(10, 5)
tautologie(f)

Et notre exemple adoré ? Est-ce une tautologie ? Est-il au moins satisfiable ?

In [ ]:
satisfiable(exemple)

In [ ]:
tautologie(exemple)

### 3.5 Tautologies incontournables

Une des tâches première du logicien en particulier et du mathématicien en général est d'écrire des tautologies. Parmi les tautologies fondamentales de la logique nous trouvons :

#### 3.5.1 La double négation

In [ ]:
double_negation = parse('--x<->x')
tautologie(double_negation)

#### 3.5.2 La non-contradiction

In [ ]:
non_contradiction = parse('-(x.-x)')
tautologie(non_contradiction)

#### 3.5.3 Le tiers exclu

In [ ]:
tiers_exclu = parse('x+-x')
tautologie(tiers_exclu)

#### 3.5.4 Les lois de Morgan

In [ ]:
morgan1 = parse('-(a.b)<->-a+-b')
tautologie(morgan1)

In [ ]:
morgan2 = parse('-(a+b)<->-a.-b')
tautologie(morgan2)

#### 3.5.5 Le modus Ponens

In [ ]:
modus_ponens = parse('x.(x->y)->y')
tautologie(modus_ponens)

#### 3.5.6 La transitivité de l'implication

In [ ]:
trans_impl = parse('(x->y).(y->z)->(x->z)')
tautologie(trans_impl)

#### 3.5.7 Le principe de contraposition

In [ ]:
contra = parse('(a->b)<->(-b->-a)')
tautologie(contra)

Et bien d'autres ... démontrez autant que vous voudrez. Quoique "démontrer" veuille maintenant dire "appuyer sur la touche Entrée" :-)